In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['公司代號'] != '公司代號']
    df = df[~df['公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[['公司代號','公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[['公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on='公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_revenue_sii = generate_df_for_stocktype(107, 1, 3, 'sii', 'Revenue', '營業收入', '綜合損益彙總表')

df_revenue_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業收入
year: 106
season: 4
營業收入
year: 106
season: 3
營業收入
year: 106
season: 2
營業收入
year: 106
season: 1
營業收入
year: 105
season: 4
營業收入
year: 105
season: 3
營業收入
year: 105
season: 2
營業收入
year: 105
season: 1
營業收入
year: 104
season: 4
營業收入
year: 104
season: 3
營業收入
year: 104
season: 2
營業收入
year: 104
season: 1


公司代號     公司名稱 Revenue(%)_107Q1 Revenue(%)_106Q4 Revenue(%)_106Q3  \
0    2801     彰化銀行              NaN              NaN              NaN   
1    2809     京城銀行              NaN              NaN              NaN   
2    2812     台中銀行              NaN              NaN              NaN   
3    2820       華票              NaN              NaN              NaN   
4    2834     臺灣企銀              NaN              NaN              NaN   
5    2836       高銀              NaN              NaN              NaN   
6    2838     聯邦銀行              NaN              NaN              NaN   
7    2845     遠東商銀              NaN              NaN              NaN   
8    2849     安泰銀行              NaN              NaN              NaN   
9    2855     統一證券              NaN              NaN              NaN   
10   2856     元富證券              NaN              NaN              NaN   
11   6005      群益證              NaN              NaN              NaN   
12   6024      群益期              NaN              NaN              NaN   
13   1101       台泥         24179214         98311776         68952108   
14   1102       亞泥         16573882         64899248         45349036   
15   1103       嘉泥           471257          2095607          1565230   
16   1104     環球水泥          1166097          4405376          3287855   
17   1108     幸福水泥           832706          3434454          2592867   
18   1109     信大水泥          1061381          5375877          3743408   
19   1110       東泥           412490          1716725          1141614   
20   1201     味全公司          3917347         17749330         13169205   
21   1203     味王公司          1447466          6195171          4633517   
22   1210     大成長城         17123119         75931014         55967032   
23   1213       大飲           149094           649522           535966   
24   1215     卜蜂企業          4957240         19865000         14759528   
25   1216       統一        104288097        399860953        305037138   
26   1217      愛之味          1028433          4146490          3371910   
27   1218     泰山企業          1844853          7681801          5852520   
28   1219     福壽實業          2880708         10822788          8016358   
29   1220       台榮           573904          2366605          1699435   
30   1225      福懋油          2794671         10757313          7970121   
31   1227       佳格          7414473         26477924         19370722   
32   1229     聯華實業          1224453          4845301          3582738   
33   1231     聯華食品          2016950          7031023          5312642   
34   1232      大統益          4117718         16884341         12700093   
35   1233       天仁           553440          2130351          1594662   
36   1234       黑松          2316158          9090115          7046095   
37   1235       興泰             6033            76878            63717   
38   1236     宏亞食品           571543          1878973          1290395   
39   1256  鮮活果汁-KY           699961          2917183          2405250   
40   1262    綠悅-KY          1276116          6296238          4867226   
41   1301       台塑         54167368        206709755        153641840   
42   1303     南亞塑膠         82219991        306139952        224643255   
43   1304       台聚         14670146         58133943         42866476   
44   1305       華夏          4144200         14701741         10928129   
45   1307     三芳化工          2385362          9855355          7653066   
46   1308       亞聚          1326214          6404467          4808117   
47   1309     台達化工          4842167         19821042         14346916   
48   1310       台苯          4004442         14750826         10945700   
49   1312     國喬石化          6386708         23350965         17079012   
50   1313       聯成         13569504         50600125         36163348   
51   1314      中石化          9494452         33335970         24388945   
52   1315     達新工業           573452          2654707          2077445   
53   1316       上曜           766579          2159740           

In [5]:
df_revenue_otc = generate_df_for_stocktype(107, 1, 3, 'otc', 'Revenue', '營業收入', '綜合損益彙總表')

df_revenue_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業收入
year: 106
season: 4
營業收入
year: 106
season: 3
營業收入
year: 106
season: 2
營業收入
year: 106
season: 1
營業收入
year: 105
season: 4
營業收入
year: 105
season: 3
營業收入
year: 105
season: 2
營業收入
year: 105
season: 1
營業收入
year: 104
season: 4
營業收入
year: 104
season: 3
營業收入
year: 104
season: 2
營業收入
year: 104
season: 1


公司代號    公司名稱 Revenue(%)_107Q1 Revenue(%)_106Q4 Revenue(%)_106Q3  \
0    6015    宏遠證券              NaN              NaN              NaN   
1    6016    康和證券              NaN              NaN              NaN   
2    6020     大展證              NaN              NaN              NaN   
3    6021     大慶證              NaN              NaN              NaN   
4    6023    元大期貨              NaN              NaN              NaN   
5    6026    福邦證券              NaN              NaN              NaN   
6    1258   其祥-KY           677719          2480922          1895168   
7    1259      安心          1235482          4919312          3697658   
8    1264      德麥           959944          3675034          2689043   
9    1333     恩得利           102652           418555           315234   
10   1336      台翰           602809          2284494          1640266   
11   1565    精華光學          1583200          6417887          4775484   
12   1566      捷邦          1289891          5311419          3958387   
13   1569      濱川           785233          3591565          2522310   
14   1570    力肯實業           135472           806650           639154   
15   1580    新麥企業           854051          4614233          3314118   
16   1584    精剛精密           191201           955679           764886   
17   1586    和勤精機           602633          2223818          1588722   
18   1591   駿吉-KY           155749           416161           316796   
19   1593      祺驊           155868           834492           610086   
20   1595    川寶科技           427347          1369985           939883   
21   1597      直得           504842          1488259          1041580   
22   1599     宏佳騰           355607          2430420          1617435   
23   1742      台蠟            93607           418837           329054   
24   1752      南光           378872          1503720          1067145   
25   1777      生泰           191471           694985           548010   
26   1781    合世生醫            89031           534459           401335   
27   1784    訊聯生技           186970           697401           506555   
28   1785     光洋科          5126362         15753593         10750655   
29   1787     福盈科           451956          1846505          1382517   
30   1788    杏昌生技           771056          2958880          2211782   
31   1795    美時製藥          1489784          6423760          4592671   
32   1799      易威            92196           374478           301662   
33   1813     寶利徠           113054           397829           308491   
34   1815    富喬工業          1157824          4812201          3758603   
35   2035    唐榮公司          4239350         18918149         14444285   
36   2061      風青           352293          1268422           907069   
37   2063      世鎧           242420           947205           696741   
38   2064      晉椿           687600          2447737          1730673   
39   2066      世德           313605          1337000           996374   
40   2067      嘉鋼           342077          1259332           884685   
41   2221    大甲永和           262646           937086           652646   
42   2230      泰茂           129601           551138           391402   
43   2233      宇隆           676108          2389410          1785828   
44   2235      謚源           181239           812066           640570   
45   2596    綠意開發           561467          1220023           846680   
46   2640     大車隊           463421          1694837          1253567   
47   2641    正德海運           163636           740251           575969   
48   2718      晶悅            54810           221892           156317   
49   2719     燦星旅           483175          2437341          1941780   
50   2724   富驛-KY           147696           757162           556124   
51   2726   雅茗-KY           525688          1994450          1487602   
52   2729    瓦城泰統          1069887          4106715          3106737   
53   2732    六角國際           793867          2497946          1794420   
54   2734     易飛網           249918          1

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_revenue = pd.concat([df_revenue_sii,df_revenue_otc],axis=0, ignore_index=True)

df_revenue

公司代號     公司名稱 Revenue(%)_107Q1 Revenue(%)_106Q4 Revenue(%)_106Q3  \
0     2801     彰化銀行              NaN              NaN              NaN   
1     2809     京城銀行              NaN              NaN              NaN   
2     2812     台中銀行              NaN              NaN              NaN   
3     2820       華票              NaN              NaN              NaN   
4     2834     臺灣企銀              NaN              NaN              NaN   
5     2836       高銀              NaN              NaN              NaN   
6     2838     聯邦銀行              NaN              NaN              NaN   
7     2845     遠東商銀              NaN              NaN              NaN   
8     2849     安泰銀行              NaN              NaN              NaN   
9     2855     統一證券              NaN              NaN              NaN   
10    2856     元富證券              NaN              NaN              NaN   
11    6005      群益證              NaN              NaN              NaN   
12    6024      群益期              NaN              NaN              NaN   
13    1101       台泥         24179214         98311776         68952108   
14    1102       亞泥         16573882         64899248         45349036   
15    1103       嘉泥           471257          2095607          1565230   
16    1104     環球水泥          1166097          4405376          3287855   
17    1108     幸福水泥           832706          3434454          2592867   
18    1109     信大水泥          1061381          5375877          3743408   
19    1110       東泥           412490          1716725          1141614   
20    1201     味全公司          3917347         17749330         13169205   
21    1203     味王公司          1447466          6195171          4633517   
22    1210     大成長城         17123119         75931014         55967032   
23    1213       大飲           149094           649522           535966   
24    1215     卜蜂企業          4957240         19865000         14759528   
25    1216       統一        104288097        399860953        305037138   
26    1217      愛之味          1028433          4146490          3371910   
27    1218     泰山企業          1844853          7681801          5852520   
28    1219     福壽實業          2880708         10822788          8016358   
29    1220       台榮           573904          2366605          1699435   
30    1225      福懋油          2794671         10757313          7970121   
31    1227       佳格          7414473         26477924         19370722   
32    1229     聯華實業          1224453          4845301          3582738   
33    1231     聯華食品          2016950          7031023          5312642   
34    1232      大統益          4117718         16884341         12700093   
35    1233       天仁           553440          2130351          1594662   
36    1234       黑松          2316158          9090115          7046095   
37    1235       興泰             6033            76878            63717   
38    1236     宏亞食品           571543          1878973          1290395   
39    1256  鮮活果汁-KY           699961          2917183          2405250   
40    1262    綠悅-KY          1276116          6296238          4867226   
41    1301       台塑         54167368        206709755        153641840   
42    1303     南亞塑膠         82219991        306139952        224643255   
43    1304       台聚         14670146         58133943         42866476   
44    1305       華夏          4144200         14701741         10928129   
45    1307     三芳化工          2385362          9855355          7653066   
46    1308       亞聚          1326214          6404467          4808117   
47    1309     台達化工          4842167         19821042         14346916   
48    1310       台苯          4004442         14750826         10945700   
49    1312     國喬石化          6386708         23350965         17079012   
50    1313       聯成         13569504         50600125         36163348   
51    1314      中石化          9494452         33335970         24388945   
52    1315     達新工業           573452          2654707          2077445   
53    1316

In [7]:
#檢查column資料型態

#df_revenue.info() #non-null object
#df_revenue.dtypes #object
#df_revenue.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
Revenue(%)_107Q1    float64
Revenue(%)_106Q4    float64
Revenue(%)_106Q3    float64
Revenue(%)_106Q2    float64
Revenue(%)_106Q1    float64
Revenue(%)_105Q4    float64
Revenue(%)_105Q3    float64
Revenue(%)_105Q2    float64
Revenue(%)_105Q1    float64
Revenue(%)_104Q4    float64
Revenue(%)_104Q3    float64
Revenue(%)_104Q2    float64
Revenue(%)_104Q1    float64
dtype: object
'''

df_revenue = df_revenue.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_revenue.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                  int64
公司名稱                 object
Revenue(%)_107Q1    float64
Revenue(%)_106Q4    float64
Revenue(%)_106Q3    float64
Revenue(%)_106Q2    float64
Revenue(%)_106Q1    float64
Revenue(%)_105Q4    float64
Revenue(%)_105Q3    float64
Revenue(%)_105Q2    float64
Revenue(%)_105Q1    float64
Revenue(%)_104Q4    float64
Revenue(%)_104Q3    float64
Revenue(%)_104Q2    float64
Revenue(%)_104Q1    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['Revenue(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['Revenue(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['Revenue(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['Revenue(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_revenue['Growth_{0}Q{1}'.format(year, season)] = df_revenue.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_revenue['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_revenue.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [14]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['有價證券代號及名稱'] != '股票']
    df = df[~df['有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df['產業別'] > '0']
    del newdf['國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf['備註']

    df2=newdf['有價證券代號及名稱'].str.split(' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if '　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split('　')[1]
            df2.iat[i,0]=df2.iat[i,0].split('　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:'公司代號',1:'股票名稱'})
    del newdf['有價證券代號及名稱']

    return newdf

In [15]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_revenue = df_revenue.merge(df_basicinfo, on='公司代號', how='inner')

df_revenue

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  Revenue(%)_107Q1  Revenue(%)_106Q4  Revenue(%)_106Q3  \
0     2801     彰化銀行               NaN               NaN               NaN   
1     2809     京城銀行               NaN               NaN               NaN   
2     2812     台中銀行               NaN               NaN               NaN   
3     2820       華票               NaN               NaN               NaN   
4     2834     臺灣企銀               NaN               NaN               NaN   
5     2836       高銀               NaN               NaN               NaN   
6     2838     聯邦銀行               NaN               NaN               NaN   
7     2845     遠東商銀               NaN               NaN               NaN   
8     2849     安泰銀行               NaN               NaN               NaN   
9     2855     統一證券               NaN               NaN               NaN   
10    2856     元富證券               NaN               NaN               NaN   
11    6005      群益證               NaN               NaN               NaN   
12    6024      群益期               NaN               NaN               NaN   
13    1101       台泥      2.417921e+07      9.831178e+07      6.895211e+07   
14    1102       亞泥      1.657388e+07      6.489925e+07      4.534904e+07   
15    1103       嘉泥      4.712570e+05      2.095607e+06      1.565230e+06   
16    1104     環球水泥      1.166097e+06      4.405376e+06      3.287855e+06   
17    1108     幸福水泥      8.327060e+05      3.434454e+06      2.592867e+06   
18    1109     信大水泥      1.061381e+06      5.375877e+06      3.743408e+06   
19    1110       東泥      4.124900e+05      1.716725e+06      1.141614e+06   
20    1201     味全公司      3.917347e+06      1.774933e+07      1.316920e+07   
21    1203     味王公司      1.447466e+06      6.195171e+06      4.633517e+06   
22    1210     大成長城      1.712312e+07      7.593101e+07      5.596703e+07   
23    1213       大飲      1.490940e+05      6.495220e+05      5.359660e+05   
24    1215     卜蜂企業      4.957240e+06      1.986500e+07      1.475953e+07   
25    1216       統一      1.042881e+08      3.998610e+08      3.050371e+08   
26    1217      愛之味      1.028433e+06      4.146490e+06      3.371910e+06   
27    1218     泰山企業      1.844853e+06      7.681801e+06      5.852520e+06   
28    1219     福壽實業      2.880708e+06      1.082279e+07      8.016358e+06   
29    1220       台榮      5.739040e+05      2.366605e+06      1.699435e+06   
30    1225      福懋油      2.794671e+06      1.075731e+07      7.970121e+06   
31    1227       佳格      7.414473e+06      2.647792e+07      1.937072e+07   
32    1229     聯華實業      1.224453e+06      4.845301e+06      3.582738e+06   
33    1231     聯華食品      2.016950e+06      7.031023e+06      5.312642e+06   
34    1232      大統益      4.117718e+06      1.688434e+07      1.270009e+07   
35    1233       天仁      5.534400e+05      2.130351e+06      1.594662e+06   
36    1234       黑松      2.316158e+06      9.090115e+06      7.046095e+06   
37    1235       興泰      6.033000e+03      7.687800e+04      6.371700e+04   
38    1236     宏亞食品      5.715430e+05      1.878973e+06      1.290395e+06   
39    1256  鮮活果汁-KY      6.999610e+05      2.917183e+06      2.405250e+06   
40    1262    綠悅-KY      1.276116e+06      6.296238e+06      4.867226e+06   
41    1301       台塑      5.416737e+07      2.067098e+08      1.536418e+08   
42    1303     南亞塑膠      8.221999e+07      3.061400e+08      2.246433e+08   
43    1304       台聚      1.467015e+07      5.813394e+07      4.286648e+07   
44    1305       華夏      4.144200e+06      1.470174e+07      1.092813e+07   
45    1307     三芳化工      2.385362e+06      9.855355e+06      7.653066e+06   
46    1308       亞聚      1.326214e+06      6.404467e+06      4.808117e+06   
47    1309     台達化工      4.842167e+06      1.982104e+07      1.434692e+07   
48    1310       台苯      4.004442e+06      1.475083e+07      1.094570e+07   
49    1312     國喬石化      6.386708e+06      2.335096e+07      1.707901e+07   
50    1313       聯成      1.356950e+07      5.060012e+07      3.616335e+07   
51

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_revenue.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_Revenue.xlsx', 'Revenue_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3', 'Growth_105Q2', '2QMAGrowth_105Q2']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
